In [1]:
import sys
sys.path.insert(1, "D:\conda\anaconda3\envs\geopandas")
import geopandas as gpd
import pandas as pd
import numpy as np
import json
import h3
import folium
import osmnx as ox
from shapely import wkt
from folium.plugins import HeatMap
from shapely.geometry import Polygon

In [2]:
import fiona
import osmnx as ox

In [3]:
import datetime
import geopandas as gpd

In [4]:
#data["class_2012"][222]

In [5]:
#data["geometry"][222]

In [6]:
data=gpd.read_file(r"E:\SK001L1_BRATISLAVA_UA2012_revised_v021.gpkg")
data

country    fua_name fua_code code_2012  \
0          SK  Bratislava  SK001L1     11230   
1          SK  Bratislava  SK001L1     12220   
2          SK  Bratislava  SK001L1     11240   
3          SK  Bratislava  SK001L1     12100   
4          SK  Bratislava  SK001L1     12300   
...       ...         ...      ...       ...   
13155      SK  Bratislava  SK001L1     11100   
13156      SK  Bratislava  SK001L1     12100   
13157      SK  Bratislava  SK001L1     12100   
13158      SK  Bratislava  SK001L1     12100   
13159      SK  Bratislava  SK001L1     32000   

                                              class_2012 prod_date  \
0      Discontinuous low density urban fabric (S.L. :...   2020-04   
1                        Other roads and associated land   2020-04   
2      Discontinuous very low density urban fabric (S...   2020-04   
3      Industrial, commercial, public, military and p...   2020-04   
4                                             Port areas   2020-04   
...                                                  ...       ...   
13155             Continuous urban fabric (S.L. : > 80%)   2020-04   
13156  Industrial, commercial, public, military and p...   2020-04   
13157  Industrial, commercial, public, military and p...   2020-04   
13158  Industrial, commercial, public, military and p...   2020-04   
13159  Herbaceous vegetation associations (natural gr...   2020-04   

          identifier    perimeter           area comment  Pop2012  \
0      16451-SK001L1  4092.237154  106559.026054    None        0   
1      16459-SK001L1  6987.130493   46015.071264    None        0   
2       4639-SK001L1  3327.063133   75560.018737    None       17   
3       6930-SK001L1  7735.530665  568681.080105    None        6   
4       7156-SK001L1  6772.685212  237323.900485    None       39   
...              ...          ...            ...     ...      ...   
13155  17682-SK001L1   279.956245    3354.822375    None        0   
13156  17683-SK001L1   683.974827    8154.324722    None        0   
13157  17685-SK001L1   300.814440    3827.502690    None        0   
13158  17684-SK001L1   834.383934   18910.681363    None        0   
13159  17686-SK001L1  2268.320653   78853.344892    None        0   

                                                geometry  
0      MULTIPOLYGON (((4862038.703 2831302.701, 48620...  
1      MULTIPOLYGON (((4850392.182 2811290.909, 48503...  
2      MULTIPOLYGON (((4858343.819 2834203.376, 48583...  
3      MULTIPOLYGON (((4841057.659 2836409.832, 48410...  
4      MULTIPOLYGON (((4851839.832 2805971.459, 48518...  
...                                                  ...  
13155  MULTIPOLYGON (((4862201.749 2800208.028, 48621...  
13156  MULTIPOLYGON (((4853070.703 2805526.497, 48530...  
13157  MULTIPOLYGON (((4865643.891 2831757.620, 48655...  
13158  MULTIPOLYGON (((4869110.964 2827263.331, 48691...  
13159  MULTIPOLYGON (((4832671.131 2827523.515, 48326...  

[13160 rows x 12 columns]

In [7]:
energydf=pd.read_excel(r'E:\data_climathon_consumption_profiles.xlsx')

In [8]:
#energydf

In [9]:
energydf["idnum"]=""

In [10]:
energydf["ID"].unique()[18] #12-18

'SME_7'

In [11]:
list(range(12,19))

[12, 13, 14, 15, 16, 17, 18]

In [12]:
energyarr=[]
idvalues=energydf["ID"].unique()
count=0
for i in range(energydf["ID"].size):
    if(energydf["ID"][i]!=idvalues[count]):
        count+=1
    if(energydf["ID"][i]==idvalues[count]):
        energyarr.append(count)    
energydf = energydf.assign(idnum=pd.Series(energyarr).values)

In [13]:
#energydf["Time"][53].minute % 30

In [14]:
deletearr=[]
for i in range(energydf["ID"].size):
    if (energydf["Time"][i].minute % 30!=0):
        deletearr.append(i)

In [15]:
energydf=energydf.drop(energydf.index[deletearr])
energydf=energydf.reset_index()
energydf

index            ID  Yday  Month  Mday      Time     Value  idnum
0            0   Household_1     1      1     1  00:00:00  0.468485      0
1            2   Household_1     1      1     1  00:30:00  0.597333      0
2            4   Household_1     1      1     1  01:00:00  0.481788      0
3            6   Household_1     1      1     1  01:30:00  0.466121      0
4            8   Household_1     1      1     1  02:00:00  0.479909      0
...        ...           ...   ...    ...   ...       ...       ...    ...
367883  735764  EV_charger_2   365     12    31  21:30:00  0.900000     20
367884  735766  EV_charger_2   365     12    31  22:00:00  0.900000     20
367885  735768  EV_charger_2   365     12    31  22:30:00  0.900000     20
367886  735770  EV_charger_2   365     12    31  23:00:00  0.900000     20
367887  735772  EV_charger_2   365     12    31  23:30:00  0.598750     20

[367888 rows x 8 columns]

In [16]:
#energydf["idnum"].value_counts()[20]

In [17]:
#energyarr=[]
#idvalues=energydf["ID"].unique()
#count=0
#for i in range(energydf["ID"].size):
#    if(energydf["idnum"][i]!=count):
#        count+=1
#    if(energydf["idnum"][i]==count):
#        energyarr.append(count)   

In [18]:
#(datetime.datetime(2017, 2, 26,0,0)+datetime.timedelta(minutes=30)).time()

In [19]:
#energydf["idnum"].value_counts()[0]/48

In [20]:
energydf["Time"][2]

datetime.time(1, 0)

In [21]:
summa1=[]
count=0
summaiter=0
for i in range(10):
    for j in range(energydf["idnum"].value_counts()[i]):
        summaiter=[]
        summaiter.append(energydf["Value"][count+j])
        #summaiter=summaiter.mean()
        summaiter=sum(summaiter)/len(summaiter)
    summa1.append(summaiter)
    count+=energydf["idnum"].value_counts()[i]

In [22]:
#summa1

In [23]:
summa=[]
count=0
summaiter=0
for i in range(10):
    start_datetime=datetime.datetime(2017, 2, 26,0,0)
    datetime_current=start_datetime
    minutes_counter=0
    for j in range(48):
        time_current=start_datetime.time()
        summaiter=[]
        time_current=(datetime_current+datetime.timedelta(minutes=30*minutes_counter)).time()
        for k in range(energydf["idnum"].value_counts()[i]):
            if(energydf["Time"][count+k]==time_current):
                summaiter.append(energydf["Value"][count+k])
        summaiter=sum(summaiter)/len(summaiter)
        summa.append(summaiter)
        minutes_counter+=1
    summa.append(summaiter)
    count+=energydf["idnum"].value_counts()[i]

In [24]:
summa_sme=[]
count=0
summaiter_sme=0
for i in range(12,19):
    start_datetime=datetime.datetime(2017, 2, 26,0,0)
    datetime_current=start_datetime
    minutes_counter=0
    for j in range(48):
        time_current=start_datetime.time()
        summaiter_sme=[]
        time_current=(datetime_current+datetime.timedelta(minutes=30*minutes_counter)).time()
        for k in range(energydf["idnum"].value_counts()[i]):
            if(energydf["Time"][count+k]==time_current):
                summaiter_sme.append(energydf["Value"][count+k])
        summaiter_sme=sum(summaiter_sme)/len(summaiter_sme)
        summa_sme.append(summaiter_sme)
        minutes_counter+=1
    summa_sme.append(summaiter_sme)
    count+=energydf["idnum"].value_counts()[i]

In [25]:
summa_shaped=np.reshape(summa, (10,49))

In [26]:
len(summa_sme)/7

49.0

In [27]:
summa_shaped_sme=np.reshape(summa_sme, (7,49))

In [28]:
#summa_shaped_sme

In [29]:
byhours=[]
for i in range(48):
    byhours.append(np.reshape(summa,(10,49))[0:,i].mean())

In [30]:
#byhours

In [31]:
#energydf

In [32]:
#energydf["Value"].mean()

In [33]:
#trees=gpd.read_file(r"E:\SK001L1_BRATISLAVA_UA2018_STL_v012.gpkg")

In [34]:
def visualize_hexagons(hexagons, color="red", folium_map=None):

    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    
    if folium_map is None:
        m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=20, tiles='cartodbpositron')
    else:
        m = folium_map
        
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color=color)
        m.add_child(my_PolyLine)
    return m
  
h3_address = h3.geo_to_h3(45.035470, 38.975313,  9) # 9 - индекс, определяющий размер гексагона                                                                                                     
visualize_hexagons([h3_address])

In [35]:
m = folium.Map(location=[48.2,17.2], zoom_start=12, tiles='CartoDB positron')

In [36]:
def visualize_polygons(geometry):
    
    lats, lons = get_lat_lon(geometry)
    
    m = folium.Map(location=[sum(lats)/len(lats), sum(lons)/len(lons)], zoom_start=13, tiles='cartodbpositron')
    
    overlay = gpd.GeoSeries(geometry).to_json()
    folium.GeoJson(overlay, name = 'boundary').add_to(m)
    
    return m

# выводим центроиды полигонов
def get_lat_lon(geometry):
        
    lon = geometry.apply(lambda x: x.x if x.type == 'Point' else x.centroid.x)
    lat = geometry.apply(lambda x: x.y if x.type == 'Point' else x.centroid.y)
    return lat, lon
  
# выгрузим границы Краснодара из OSM
cities = ['Bratislava']
polygon_krd = ox.geometries_from_place(cities, {'boundary':'administrative'}).reset_index()
polygon_krd = polygon_krd[(polygon_krd['name'] == 'Bratislava')]
# посмотрим что получилось
visualize_polygons(polygon_krd['geometry'])

In [37]:
def create_hexagons(geoJson):
    
    polyline = geoJson['coordinates'][0]

    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat)/len(lat), sum(lng)/len(lng)], zoom_start=13, tiles='cartodbpositron')
    my_PolyLine=folium.PolyLine(locations=polyline,weight=8,color="green")
    m.add_child(my_PolyLine)

    hexagons = list(h3.polyfill(geoJson, 9.5))
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v:v[0],polyline))
        lng.extend(map(lambda v:v[1],polyline))
        polylines.append(polyline)
    for polyline in polylines:
        my_PolyLine=folium.PolyLine(locations=polyline,weight=3,color='red')
        m.add_child(my_PolyLine)
        
    polylines_x = []
    for j in range(len(polylines)):
        a = np.column_stack((np.array(polylines[j])[:,1],np.array(polylines[j])[:,0])).tolist()
        polylines_x.append([(a[i][0], a[i][1]) for i in range(len(a))])
        
    polygons_hex = pd.Series(polylines_x).apply(lambda x: Polygon(x))
        
    return m, polygons_hex, polylines
# polygon_hex , polylines - геометрии гексагонов в разных форматах

# сгенерим гексагоны внутри полигона г. Краснодар
geoJson = json.loads(gpd.GeoSeries(polygon_krd['geometry']).to_json())
geoJson = geoJson['features'][0]['geometry']
geoJson = {'type':'Polygon','coordinates': [np.column_stack((np.array(geoJson['coordinates'][0])[:, 1],
                                                      np.array(geoJson['coordinates'][0])[:, 0])).tolist()]}

m, polygons, polylines = create_hexagons(geoJson)
m

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [38]:
polylines[0]

[(48.24754930530205, 17.08476810900287),
 (48.249298712407544, 17.084734871955604),
 (48.25010503841365, 17.082307024294895),
 (48.24916194036562, 17.079912487936422),
 (48.24741254118716, 17.079945836083443),
 (48.24660623212822, 17.08237360949017),
 (48.24754930530205, 17.08476810900287)]

In [39]:
#gdfs

In [40]:
def osm_query(tag, city):
    gdf = ox.geometries_from_place(city, tag).reset_index()
    gdf['city'] = np.full(len(gdf), city.split(',')[0])
    gdf['object'] = np.full(len(gdf), list(tag.keys())[0])
    gdf['type'] = np.full(len(gdf), tag[list(tag.keys())[0]])
    gdf = gdf[['city', 'object', 'type', 'geometry']]
    print(gdf.shape)
    return gdf
  
 # Выгрузим интересующие нас категории объектов 
tags = [
        {'building' : 'apartments'}, {'building' : 'detached'}, 
        {'building' : 'dormitory'}, {'building' : 'hotel'}, 
        {'building' : 'house'}, {'building' : 'semidetached_house'}, 
        {'building' : 'terrace'},  {'building' : 'commercial'},
        {'building' : 'office'},  {'building' : 'terrace'},  
        {'building' : 'terrace'}, {'building':'retail'}, 
        {'building':'train_station'},
        {'highway' : 'bus_stop'}, {'footway':'crossing'},
        {'amenity':'cafe'}, {'amenity':'fast_food'}, 
        {'amenity':'restaurant'}, {'amenity':'college'}, 
        {'amenity':'language_school'},  {'amenity':'school'},  
        {'amenity':'university'},  {'amenity':'atm'},  
        {'amenity':'bank'},  {'amenity':'clinic'},  
        {'amenity':'hospital'},  {'amenity':'pharmacy'},  
        {'amenity':'theatre'},  {'amenity':'townhall'},  
        {'amenity':'bench'}, 
       ]
cities = ['Bratislava, Slovakia']

gdfs = []
for city in cities:
    for tag in tags:
        gdfs.append(osm_query(tag, city))
        
# посмотрим что получилось
data_poi = pd.concat(gdfs)
data_poi.groupby(['city','object','type'], as_index = False).agg({'geometry':'count'})

# добавим координаты/центроиды
lat, lon = get_lat_lon(data_poi['geometry'])
data_poi['lat'] = lat
data_poi['lon'] = lon

(5710, 4)
(2691, 4)
(57, 4)
(45, 4)
(1393, 4)
(49, 4)
(48, 4)
(243, 4)
(387, 4)
(48, 4)
(48, 4)
(358, 4)
(17, 4)
(1267, 4)
(1883, 4)
(443, 4)
(462, 4)
(712, 4)
(5, 4)
(10, 4)
(224, 4)
(34, 4)
(413, 4)
(169, 4)
(44, 4)
(10, 4)
(219, 4)
(39, 4)
(20, 4)
(1919, 4)


In [41]:
# sjoin - spatial join - пересекаем гексагоны с объектами (определяем какие объекты находятся в разрезе каждого гексагона)

gdf_1 = gpd.GeoDataFrame(data_poi, geometry=gpd.points_from_xy(data_poi.lon, data_poi.lat))

gdf_2 = pd.DataFrame(polygons, columns = ['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)
gdf_2 = gdf_2.merge(geometry_uniq, on = 'geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')

itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
itog_table = itog_table.dropna()
itog_table.head()

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
D:\Conda\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3357: FutureWarning: The `op` parameter is deprecated and will be removed in a future release. Please use the `predicate` parameter instead.
  if (await self.run_code(code, result,  async_=asy)):


geometry  \
3  POLYGON ((17.11989 48.17499, 17.11986 48.17674...   
3  POLYGON ((17.11989 48.17499, 17.11986 48.17674...   
3  POLYGON ((17.11989 48.17499, 17.11986 48.17674...   
3  POLYGON ((17.11989 48.17499, 17.11986 48.17674...   
3  POLYGON ((17.11989 48.17499, 17.11986 48.17674...   

                                           polylines id  index_right  \
3  [(48.174988509261965, 17.11988791647317), (48....  3       1456.0   
3  [(48.174988509261965, 17.11988791647317), (48....  3        319.0   
3  [(48.174988509261965, 17.11988791647317), (48....  3       1464.0   
3  [(48.174988509261965, 17.11988791647317), (48....  3       2640.0   
3  [(48.174988509261965, 17.11988791647317), (48....  3        902.0   

         city    object      type        lat        lon  
3  Bratislava  building  detached  48.174533  17.117647  
3  Bratislava   highway  bus_stop  48.174893  17.116767  
3  Bratislava  building  detached  48.174989  17.119854  
3  Bratislava  building  detached  48.174993  17.115902  
3  Bratislava   highway  bus_stop  48.175742  17.116803

In [42]:
def create_choropleth(data, json, columns, legend_name, feature, bins):
    
    lat, lon = get_lat_lon(data['geometry'])

    m = folium.Map(location=[sum(lat)/len(lat), sum(lon)/len(lon)], zoom_start=13, tiles='cartodbpositron')
    
    folium.Choropleth(
        geo_data=json,
        name="choropleth",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="YlGn",
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name=legend_name,
        nan_fill_color = 'black',
        bins = bins

    ).add_to(m)

    folium.LayerControl().add_to(m)

    return m
  
# подготовим данные 
itog_table['geometry'] = itog_table['geometry'].astype(str) #для groupby
itog_table['id'] = itog_table['id'].astype(str) #для Choropleth
agg_all = itog_table.groupby(['geometry','type','id'], as_index = False).agg({'lat':'count'}).rename(columns = {'lat':'counts'})
agg_all['geometry'] = agg_all['geometry'].apply(wkt.loads) #возвращаем формат геометрий

agg_all_cafe = agg_all.query("type == 'cafe'")[["geometry","counts",'id']]
agg_all_cafe['id'] = agg_all_cafe['id'].astype(str)
data_geo_1 = gpd.GeoSeries(agg_all_cafe.set_index('id')["geometry"]).to_json()

create_choropleth(agg_all_cafe, data_geo_1, ["id","counts"], 'Cafe counts', 'counts', 5)
    

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
D:\Conda\anaconda3\lib\site-packages\geopandas\geodataframe.py:1350: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


In [43]:
gdf_aparts = ox.geometries_from_place(city, {'building' : 'apartments'}).reset_index()
gdf_workspaces = ox.geometries_from_place(city, {'building' : 'apartments'}).reset_index()
# полнота building:levels (этажи)
print(np.round(len(gdf_aparts['building:levels'].dropna())/len(gdf_aparts['building:levels']), 2))

# полнота building:flats (квартиры)
#print(np.round(len(gdf_aparts['building:flats'].dropna())/len(gdf_aparts['building:flats']), 2))/parts['building:flats'].dropna()/len(gdf_aparts['building:flats']), 2))

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


0.71


In [44]:
lat_g, lon_g = get_lat_lon(gdf_aparts['geometry'])
gdf_aparts['lat'] = lat_g
gdf_aparts['lon'] = lon_g

apartments = ['apartments' , 'dormitory']
houses = ['house', 'semidetached_house', 'detached', 'terrace']
people_ctn = []

itog_table_people = itog_table.merge(gdf_aparts[['lat', 'lon', 'building:levels']], on = ['lat', 'lon'], how = 'left')
itog_table_people['building:levels'] = itog_table_people['building:levels'].fillna(1)
itog_table_people = itog_table_people.rename(columns = {'building:levels' : 'levels'})

itog_table_people = itog_table_people.sample(frac=1).reset_index(drop=True)


D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [45]:
itog_table_people.head()

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


geometry  \
0  POLYGON ((17.12043842632633 48.14521395445991,...   
1  POLYGON ((17.13443881561294 48.17013881046032,...   
2  POLYGON ((17.1185003247399 48.11974178442513, ...   
3  POLYGON ((17.16822914468848 48.16757135478792,...   
4  POLYGON ((17.16851059842906 48.15180729892658,...   

                                           polylines    id  index_right  \
0  [(48.14521395445991, 17.120438426326334), (48....  2861        174.0   
1  [(48.170138810460315, 17.134438815612942), (48...  2870        116.0   
2  [(48.11974178442513, 17.118500324739898), (48....  2614        735.0   
3  [(48.16757135478792, 17.168229144688482), (48....  2415       1208.0   
4  [(48.151807298926585, 17.16851059842906), (48....  2984          9.0   

         city    object      type        lat        lon levels  
0  Bratislava  building    office  48.146477  17.121890      1  
1  Bratislava  building     house  48.170617  17.133465      1  
2  Bratislava   footway  crossing  48.121452  17.117348      1  
3  Bratislava  building  detached  48.168696  17.168906      1  
4  Bratislava  building    retail  48.150841  17.172052      1

In [46]:
apartments = ['apartments' , 'dormitory']
houses = ['house', 'semidetached_house', 'detached', 'terrace']
people_ctn = []
count_h=0

for i in range(len(itog_table_people)):
    
    if itog_table_people['type'].iloc[i] in apartments or itog_table_people['type'].iloc[i] in houses:
        count_h+=1
values=[]
values_full=[]
#summa_shaped[0:,1]
for k in range(48):
    values=[]
    for i in range(10):
        for j in range(count_h//10):
            values.append(summa_shaped[i,k])
        values.append(summa_shaped[0,0])
    values_full.append(values)

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [47]:
len(values_full[0])

10040

In [48]:
count_h

10037

In [49]:
sme = ['office', 'bank', 'commercial', 'retail']
people_ctn = []
count_s=0

for i in range(len(itog_table_people)):
    
    if itog_table_people['type'].iloc[i] in sme:
        count_s+=1
values_sme=[]
values_full_sme=[]
#summa_shaped[0:,1]
for k in range(48):
    values_sme=[]
    for i in range(7):
        for j in range(count_s//7):
            values_sme.append(summa_shaped_sme[i,k])
        values_sme.append(summa_shaped_sme[0,0])
    values_full_sme.append(values_sme)

In [50]:
count=0
for i in range(len(itog_table_people)):
    
    if itog_table_people['type'].iloc[i] in apartments or itog_table_people['type'].iloc[i] in houses:
        count+=1
count

10037

In [55]:
lat_g, lon_g = get_lat_lon(gdf_aparts['geometry'])
gdf_aparts['lat'] = lat_g
gdf_aparts['lon'] = lon_g

#{'building' : 'office'}  {'amenity':'bank'}   {'building' : 'commercial'}   {'building':'retail'}  - для коммерческих


# в среднем возьмем 3 чел. на семью

hour=14
people_ctn=[]
counter_h=0
counter_s=0
for i in range(len(itog_table_people)):
    
    if itog_table_people['type'].iloc[i] in apartments:
        
        people=values_full[hour][counter_h]
        counter_h+=1
    elif itog_table_people['type'].iloc[i] in houses:
        
        people=values_full[hour][counter_h]
        counter_h+=1
    elif itog_table_people['type'].iloc[i] in sme:
        
        people=values_full_sme[hour][counter_s]
        counter_s+=1
    else:
        people = 'not living area'
        
    people_ctn.append(people)
    
itog_table_people['count_people'] = people_ctn

table_people = itog_table_people.query("count_people != 'not living area'")
table_people['count_people'] = table_people['count_people'].astype(int)

D:\Conda\anaconda3\lib\site-packages\geopandas\geodataframe.py:1351: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


In [52]:
len(itog_table_people)//10

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


1895

In [53]:
def create_heatmap(data, lat_lon_feature):
    
    m = folium.Map(location=[sum(data['lat'])/len(data['lat']), sum(data['lon'])/len(data['lon'])], zoom_start=13, tiles='cartodbpositron')
    
    HeatMap(data[lat_lon_feature].groupby(lat_lon_feature[0:2]).sum().reset_index().values.tolist(), 
                    radius = 60, min_opacity = 0.6, max_val = int((data[lat_lon_feature[2]]).quantile([0.75])), blur=25).add_to(m)
    return m
  
# карта плотности населения
create_heatmap(table_people, ['lat', 'lon', 'count_people'])

In [56]:
def create_heatmap(data, lat_lon_feature):
    
    m = folium.Map(location=[sum(data['lat'])/len(data['lat']), sum(data['lon'])/len(data['lon'])], zoom_start=13, tiles='cartodbpositron')
    
    HeatMap(data[lat_lon_feature].groupby(lat_lon_feature[0:2]).sum().reset_index().values.tolist(), 
                    radius = 60, min_opacity = 0.6, max_val = int((data[lat_lon_feature[2]]).quantile([0.75])), blur=25).add_to(m)
    return m
  
# карта плотности населения
create_heatmap(table_people, ['lat', 'lon', 'count_people'])

D:\Conda\anaconda3\lib\site-packages\ipykernel\ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
